In [1]:
import os, sys
# project_path = '../'
PWD = os.getenv('PWD')
# os.chdir(project_path)
sys.path.insert(0, PWD)
# sys.path.insert(0, project_path)
print(sys.path)
# os.environ.setdefault("DJANGO_SETTINGS_MODULE", "settings.py")
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"
import django
django.setup()

['/home/mpatlas/projects/django_mpatlas', '/home/mpatlas/projects/django_mpatlas/notebooks', '/home/mpatlas/projects/django_mpatlas', '/home/mpatlas/virtualenvs/py3_mpatlas/lib/python38.zip', '/home/mpatlas/virtualenvs/py3_mpatlas/lib/python3.8', '/home/mpatlas/virtualenvs/py3_mpatlas/lib/python3.8/lib-dynload', '/usr/lib/python3.8', '', '/home/mpatlas/virtualenvs/py3_mpatlas/lib/python3.8/site-packages', '/home/mpatlas/virtualenvs/py3_mpatlas/lib/python3.8/site-packages/IPython/extensions', '/home/mpatlas/.ipython']


In [2]:
%%javascript

window.scroll_flag = true
window.scroll_exit = false
window.scroll_delay = 100

$(".output_scroll").each(function() {
    $(this)[0].scrollTop = $(this)[0].scrollHeight;
});

function callScrollToBottom() {
    setTimeout(scrollToBottom, window.scroll_delay);
}

function scrollToBottom() {
    if (window.scroll_exit) {
        return;
    }
    if (!window.scroll_flag) {
        callScrollToBottom();
        return;
    };
    
    $(".output_scroll").each(function() {
        if (!$(this).attr('scroll_checkbox')){
            window.scroll_flag = true;
            $(this).attr('scroll_checkbox',true);
            var div = document.createElement('div');
            var checkbox = document.createElement('input');
            checkbox.type = "checkbox";
            checkbox.onclick = function(){window.scroll_flag = checkbox.checked}
            checkbox.checked = "checked"
            div.append("Auto-Scroll-To-Bottom: ");
            div.append(checkbox);
            $(this).parent().before(div);
        }
        
        $(this)[0].scrollTop = $(this)[0].scrollHeight;
    });
    callScrollToBottom();
}
scrollToBottom();

<IPython.core.display.Javascript object>

In [3]:
from mpa.models import Mpa, mpa_post_save
from django.db.models.signals import post_save, post_delete
from mpa.views import mpas_all_nogeom
import reversion
from reversion.models import Revision
from reversion.models import Version
import datetime
from django.db.models import Q, F, Func
from wdpa.models import WdpaPoly_prev, WdpaPoint_prev
from wdpa.models import WdpaPoly_new, WdpaPoint_new

In [4]:
logprefix = '/home/mpatlas/workspace/log/'
# logprefix = '/Users/russmo/Code/wdpa/log/'

In [5]:
mpaset = mpas_all_nogeom.exclude(
        Q(country__icontains='USA') | Q(sovereign__icontains='USA') |
        Q(country__icontains='UMI') | Q(sovereign__icontains='UMI') |
        Q(country__icontains='VIR') | Q(sovereign__icontains='VIR') |
        Q(country__icontains='PRI') | Q(sovereign__icontains='PRI') |
        Q(country__icontains='ASM') | Q(sovereign__icontains='ASM') |
        Q(country__icontains='GUM') | Q(sovereign__icontains='GUM') |
        Q(country__icontains='MNP') | Q(sovereign__icontains='MNP')
    ).filter(
        Q()
    )
mpaset.values('country').distinct()

<QuerySet [{'country': 'ABNJ'}, {'country': 'MDG'}, {'country': 'TZA'}, {'country': 'PLW'}, {'country': 'GGY'}, {'country': 'NLD'}, {'country': 'VEN'}, {'country': 'BMU'}, {'country': 'FIN/SWE'}, {'country': 'COG'}, {'country': 'CUB'}, {'country': 'MAF'}, {'country': 'IRL'}, {'country': 'GIB'}, {'country': 'IOT'}, {'country': 'ISR'}, {'country': 'GBR'}, {'country': 'BGD/IND'}, {'country': 'GMB'}, {'country': 'MMR'}, '...(remaining elements truncated)...']>

In [6]:
# mpaset = mpas_all_nogeom.exclude(
#         Q(country__icontains='USA') | Q(sovereign__icontains='USA') |
#         Q(country__icontains='UMI') | Q(sovereign__icontains='UMI') |
#         Q(country__icontains='VIR') | Q(sovereign__icontains='VIR') |
#         Q(country__icontains='PRI') | Q(sovereign__icontains='PRI') |
#         Q(country__icontains='ASM') | Q(sovereign__icontains='ASM') |
#         Q(country__icontains='GUM') | Q(sovereign__icontains='GUM') |
#         Q(country__icontains='MNP') | Q(sovereign__icontains='MNP')
#     ).exclude(
#         Q(country__icontains='MEX') | Q(country__icontains='CHL') | Q(country__icontains='IDN') | 
#         Q(country__icontains='CHN') | Q(country__icontains='JPN') | 
#         Q(sovereign__icontains='MEX') | Q(sovereign__icontains='CHL') | Q(sovereign__icontains='IDN') |
#         Q(sovereign__icontains='CHN') | Q(sovereign__icontains='JPN')
#     ).exclude(
#         Q(country__icontains='FRA') | Q(sovereign__icontains='FRA') |
#         Q(country__icontains='ATF') | Q(country__icontains='BLM') | Q(country__icontains='GLP') |
#         Q(country__icontains='GUF') | Q(country__icontains='MAF') | Q(country__icontains='MTQ') |
#         Q(country__icontains='MYT') | Q(country__icontains='NCL') | Q(country__icontains='PYF') |
#         Q(country__icontains='REU') | Q(country__icontains='SHN') | Q(country__icontains='SYC')
#     ).exclude(
#         Q(country__icontains='AUS') | Q(sovereign__icontains='AUS') |
#         Q(country__icontains='ZAF') | Q(sovereign__icontains='ZAF') |
#         Q(country__icontains='CAN') | Q(sovereign__icontains='CAN')
#     ).exclude(
#         Q(country__icontains='GBR') | Q(sovereign__icontains='GBR') |
#         Q(country__icontains='AIA') | Q(country__icontains='BMU') | Q(country__icontains='CYM') |
#         Q(country__icontains='FLK') | Q(country__icontains='GIB') | Q(country__icontains='IMN') |
#         Q(country__icontains='IOT') | Q(country__icontains='JEY') | Q(country__icontains='MSR') |
#         Q(country__icontains='PCN') | Q(country__icontains='SGS') | Q(country__icontains='SHN') |
#         Q(country__icontains='TCA') | Q(country__icontains='VGB')
#     )
# mpaset.values('country').distinct()

In [6]:
mpas_all_nogeom.filter(wdpa_id=0).update(wdpa_id=None)
mpas_all_nogeom.filter(wdpa_id=0).count()

0

In [119]:
count = 0
# cutoff_date = datetime.datetime(2018, 10, 15)
cutoff_date = datetime.datetime(2019, 12, 30)
for m in mpaset:
    versions = Version.objects.get_for_object(m)
    created = 'Never'
    if not m.wdpa_id: continue
    try:
        created = versions.first().revision.date_created
        if created > cutoff_date:
            count = count + 1
            print(count, created, 'count:', len(versions), 'mpa_id:', m.mpa_id, 'wdpa_id:', m.wdpa_id)
    except:
        pass

1 2022-04-06 13:57:48.621988 count: 2 mpa_id: 68819751 wdpa_id: 555548204
2 2022-04-06 13:58:16.673857 count: 2 mpa_id: 68819752 wdpa_id: 555548204
3 2022-04-06 13:58:56.556234 count: 2 mpa_id: 68819753 wdpa_id: 555548204
4 2022-02-16 17:09:06.467477 count: 2 mpa_id: 68819743 wdpa_id: 99653
5 2021-09-24 13:57:09.552274 count: 3 mpa_id: 68812195 wdpa_id: 555557228
6 2021-09-24 17:06:42.873498 count: 2 mpa_id: 68818611 wdpa_id: 555624907
7 2021-09-24 17:06:53.777181 count: 2 mpa_id: 68818610 wdpa_id: 555624907
8 2021-09-24 17:07:03.989614 count: 2 mpa_id: 68818609 wdpa_id: 555624907
9 2020-12-22 06:02:23.543826 count: 1 mpa_id: 68819066 wdpa_id: 555703722
10 2021-09-24 17:09:22.369447 count: 3 mpa_id: 68808362 wdpa_id: 555624907
11 2021-09-24 17:40:50.236451 count: 4 mpa_id: 68813339 wdpa_id: 555645488
12 2021-09-24 17:44:56.868053 count: 2 mpa_id: 68818983 wdpa_id: 555697868
13 2020-12-22 20:08:40.528297 count: 2 mpa_id: 6713 wdpa_id: 67916
14 2020-12-22 05:53:13.370275 count: 1 mpa_id:

115 2020-12-22 13:59:42.795426 count: 2 mpa_id: 1641 wdpa_id: 24483
116 2020-12-22 17:17:14.353407 count: 2 mpa_id: 68816001 wdpa_id: 555551355
117 2020-12-22 05:53:26.518929 count: 1 mpa_id: 68817850 wdpa_id: 555706539
118 2020-12-22 13:14:18.201283 count: 3 mpa_id: 3281 wdpa_id: 156590
119 2020-12-22 19:01:38.174891 count: 2 mpa_id: 68813107 wdpa_id: 555624892
120 2020-12-22 15:20:20.576395 count: 2 mpa_id: 6625 wdpa_id: 40940
121 2020-12-22 17:28:34.527947 count: 2 mpa_id: 15034 wdpa_id: 555558253
122 2020-12-22 16:25:33.192545 count: 2 mpa_id: 13625 wdpa_id: 555538230
123 2020-12-22 17:07:33.357839 count: 2 mpa_id: 14525 wdpa_id: 555547878
124 2020-01-01 14:55:18.042125 count: 1 mpa_id: 12131 wdpa_id: 394899
125 2020-12-22 12:50:46.809565 count: 3 mpa_id: 68813860 wdpa_id: 137747
126 2020-12-22 13:00:57.475980 count: 3 mpa_id: 68810769 wdpa_id: 149820
127 2020-12-22 13:11:23.391546 count: 3 mpa_id: 10357 wdpa_id: 156142
128 2020-12-22 13:20:00.506121 count: 3 mpa_id: 68814258 wdpa_

231 2020-12-22 13:26:11.354471 count: 2 mpa_id: 68809874 wdpa_id: 174722
232 2020-12-22 18:14:27.140000 count: 2 mpa_id: 68810366 wdpa_id: 555581076
233 2020-12-22 06:02:11.299089 count: 1 mpa_id: 68819039 wdpa_id: 555703357
234 2020-12-22 06:11:38.845503 count: 2 mpa_id: 68813528 wdpa_id: 159484
235 2020-12-22 18:10:41.906701 count: 2 mpa_id: 68812397 wdpa_id: 555580028
236 2020-12-22 15:02:32.791002 count: 2 mpa_id: 68815280 wdpa_id: 387856
237 2020-12-22 16:10:42.967883 count: 2 mpa_id: 13366 wdpa_id: 555532954
238 2020-12-22 14:10:57.060280 count: 2 mpa_id: 3886 wdpa_id: 305353
239 2020-12-22 17:06:35.941908 count: 2 mpa_id: 14476 wdpa_id: 555547828
240 2020-12-22 15:28:34.545758 count: 2 mpa_id: 540 wdpa_id: 5302
241 2020-12-22 13:03:13.256554 count: 3 mpa_id: 10087 wdpa_id: 151226
242 2020-12-22 13:22:23.272510 count: 2 mpa_id: 10693 wdpa_id: 170711
243 2020-12-22 06:03:10.109638 count: 1 mpa_id: 68819147 wdpa_id: 555704949
244 2020-12-22 06:11:04.611389 count: 2 mpa_id: 6180 wdp

346 2020-12-22 14:18:08.828616 count: 2 mpa_id: 4177 wdpa_id: 306508
347 2020-12-22 15:37:01.670852 count: 2 mpa_id: 5661 wdpa_id: 555515517
348 2020-01-01 15:12:52.452957 count: 1 mpa_id: 5672 wdpa_id: 555515594
349 2020-12-22 17:33:15.011925 count: 2 mpa_id: 15098 wdpa_id: 555559303
350 2020-12-22 15:12:26.899249 count: 2 mpa_id: 12019 wdpa_id: 392931
351 2020-12-22 12:46:56.381569 count: 3 mpa_id: 68809660 wdpa_id: 135758
352 2020-12-22 06:13:34.343682 count: 2 mpa_id: 9680 wdpa_id: 555549153
353 2020-12-22 18:22:50.757853 count: 2 mpa_id: 68816401 wdpa_id: 555587589
354 2020-12-22 05:53:43.523679 count: 1 mpa_id: 68818156 wdpa_id: 555706850
355 2020-12-22 05:52:58.107178 count: 1 mpa_id: 68817331 wdpa_id: 555706014
356 2020-12-22 06:12:03.248813 count: 2 mpa_id: 6975 wdpa_id: 220261
357 2020-12-22 14:38:22.246834 count: 2 mpa_id: 68811091 wdpa_id: 326739
358 2020-12-22 18:01:54.100015 count: 2 mpa_id: 15738 wdpa_id: 555578641
359 2020-12-22 16:06:19.729745 count: 2 mpa_id: 13225 wd

462 2020-12-22 13:10:28.890063 count: 3 mpa_id: 10281 wdpa_id: 156038
463 2020-12-22 05:56:19.903964 count: 1 mpa_id: 68818583 wdpa_id: 555622037
464 2020-12-22 16:25:27.597245 count: 2 mpa_id: 13624 wdpa_id: 555538227
465 2020-12-22 13:32:32.959449 count: 2 mpa_id: 10887 wdpa_id: 181257
466 2020-12-22 17:13:41.408146 count: 2 mpa_id: 14721 wdpa_id: 555549190
467 2020-12-22 14:14:28.965708 count: 2 mpa_id: 1764 wdpa_id: 30595
468 2020-12-22 15:32:58.453447 count: 2 mpa_id: 5525 wdpa_id: 555512338
469 2020-12-22 05:58:55.310338 count: 1 mpa_id: 68818873 wdpa_id: 555691639
470 2020-12-22 17:06:51.913768 count: 2 mpa_id: 14488 wdpa_id: 555547840
471 2020-12-22 17:00:00.461070 count: 2 mpa_id: 14217 wdpa_id: 555543690
472 2020-12-22 15:04:27.523609 count: 2 mpa_id: 11823 wdpa_id: 388434
473 2020-12-22 05:58:42.740305 count: 1 mpa_id: 68818846 wdpa_id: 555691182
474 2020-12-22 15:33:07.367691 count: 2 mpa_id: 5533 wdpa_id: 555512346
475 2020-01-01 13:57:10.286477 count: 1 mpa_id: 68811022 w

...

20886 2020-12-22 13:43:24.109807 count: 2 mpa_id: 1460 wdpa_id: 19458
20887 2020-12-22 05:53:55.852859 count: 1 mpa_id: 68818381 wdpa_id: 555707077
20888 2020-12-22 05:53:58.445216 count: 1 mpa_id: 68818428 wdpa_id: 555707124
20889 2020-12-22 20:17:24.649370 count: 2 mpa_id: 6755 wdpa_id: 81021
20890 2020-12-22 13:15:23.533486 count: 3 mpa_id: 214 wdpa_id: 1592
20891 2020-12-22 06:12:22.764561 count: 2 mpa_id: 16075 wdpa_id: 315534
20892 2020-12-22 18:50:35.992128 count: 2 mpa_id: 68812946 wdpa_id: 555622342
20893 2020-12-22 18:14:00.827176 count: 2 mpa_id: 68810349 wdpa_id: 555581024
20894 2020-12-22 06:11:05.699116 count: 2 mpa_id: 6185 wdpa_id: 13223
20895 2020-12-22 12:38:55.019409 count: 3 mpa_id: 68813696 wdpa_id: 126356
20896 2020-12-22 20:26:37.287712 count: 2 mpa_id: 729 wdpa_id: 9081
20897 2020-12-22 13:23:57.530964 count: 2 mpa_id: 3352 wdpa_id: 173030
20898 2020-12-22 15:42:40.231408 count: 2 mpa_id: 12606 wdpa_id: 555522525
20899 2020-12-22 17:45:05.710861 count: 2 mpa_id:

20997 2020-12-22 14:00:57.310053 count: 2 mpa_id: 68808380 wdpa_id: 2628
20998 2020-12-22 18:03:36.264655 count: 2 mpa_id: 15811 wdpa_id: 555578714
20999 2020-12-22 05:53:02.340092 count: 1 mpa_id: 68817408 wdpa_id: 555706092
21000 2020-12-22 05:53:20.609536 count: 1 mpa_id: 68817742 wdpa_id: 555706430
21001 2020-12-22 16:32:58.306499 count: 2 mpa_id: 68809102 wdpa_id: 555539580
21002 2020-12-22 19:59:36.919292 count: 2 mpa_id: 1952 wdpa_id: 61958
21003 2020-12-22 13:06:39.226351 count: 3 mpa_id: 3216 wdpa_id: 153033
21004 2020-12-22 05:53:41.814905 count: 1 mpa_id: 68818125 wdpa_id: 555706819
21005 2020-12-22 05:53:24.273111 count: 1 mpa_id: 68817809 wdpa_id: 555706498
21006 2020-12-22 05:53:22.416995 count: 1 mpa_id: 68817775 wdpa_id: 555706464
21007 2020-12-22 13:14:26.085855 count: 3 mpa_id: 10622 wdpa_id: 156622
21008 2020-12-22 13:07:43.803762 count: 3 mpa_id: 68814137 wdpa_id: 153533
21009 2020-12-22 15:01:52.895366 count: 2 mpa_id: 11736 wdpa_id: 387516
21010 2020-12-22 17:02:1

21123 2021-05-14 11:27:57.970014 count: 4 mpa_id: 901 wdpa_id: 11753
21124 2020-12-22 14:00:39.268137 count: 2 mpa_id: 68808375 wdpa_id: 2628
21125 2020-12-22 18:20:25.857028 count: 2 mpa_id: 68812504 wdpa_id: 555583346
21126 2020-12-22 18:20:26.966489 count: 2 mpa_id: 68812505 wdpa_id: 555583347
21127 2020-12-22 18:20:32.901284 count: 2 mpa_id: 68812512 wdpa_id: 555583375
21128 2020-12-22 19:54:32.034782 count: 2 mpa_id: 68817008 wdpa_id: 555643566
21129 2020-12-22 19:55:58.271233 count: 2 mpa_id: 68817042 wdpa_id: 555645461
21130 2020-12-22 19:56:17.854254 count: 2 mpa_id: 68817052 wdpa_id: 555645473
21131 2020-12-22 19:56:25.137666 count: 2 mpa_id: 68817058 wdpa_id: 555645480
21132 2021-06-07 13:11:49.919184 count: 2 mpa_id: 68819350 wdpa_id: 555714472
21133 2020-12-22 12:43:58.343870 count: 3 mpa_id: 172 wdpa_id: 1334
21134 2020-12-22 13:43:26.090985 count: 2 mpa_id: 68814502 wdpa_id: 194583
21135 2020-12-22 15:12:44.524665 count: 2 mpa_id: 12036 wdpa_id: 392948
21136 2020-12-22 16

21244 2020-12-22 14:22:46.947710 count: 2 mpa_id: 11200 wdpa_id: 308348
21245 2020-12-22 05:56:48.423083 count: 1 mpa_id: 68818627 wdpa_id: 555637383
21246 2020-12-22 20:04:15.941934 count: 1 mpa_id: 68819523 wdpa_id: 67043
21247 2020-12-22 15:38:06.635979 count: 1 mpa_id: 68819477 wdpa_id: 555516380
21248 2020-12-22 15:59:07.425293 count: 2 mpa_id: 12972 wdpa_id: 555527957
21249 2020-12-22 17:08:55.808073 count: 2 mpa_id: 68815957 wdpa_id: 555548066
21250 2020-12-22 14:24:46.228015 count: 2 mpa_id: 4332 wdpa_id: 308674
21251 2020-12-22 05:53:15.681838 count: 1 mpa_id: 68817652 wdpa_id: 555706340
21252 2020-12-22 12:53:34.905907 count: 3 mpa_id: 68809782 wdpa_id: 139680
21253 2020-12-22 15:42:23.511882 count: 2 mpa_id: 5762 wdpa_id: 555522511
21254 2020-12-22 05:53:44.843475 count: 1 mpa_id: 68818180 wdpa_id: 555706874
21255 2020-12-22 17:04:27.043931 count: 2 mpa_id: 14394 wdpa_id: 555547514
21256 2020-12-22 14:33:20.150733 count: 2 mpa_id: 4791 wdpa_id: 314901
21257 2020-12-22 13:22:

21364 2020-12-22 17:04:00.395778 count: 2 mpa_id: 68815946 wdpa_id: 555547162
21365 2020-12-22 06:02:13.297209 count: 1 mpa_id: 68819043 wdpa_id: 555703368
21366 2020-12-22 12:54:39.202616 count: 3 mpa_id: 68813900 wdpa_id: 139953
21367 2020-12-22 06:11:52.228848 count: 2 mpa_id: 68813543 wdpa_id: 181969
21368 2020-12-22 13:28:26.416165 count: 2 mpa_id: 10825 wdpa_id: 175544
21369 2020-12-22 06:11:35.793607 count: 2 mpa_id: 7706357 wdpa_id: 15754
21370 2020-12-22 17:46:29.068094 count: 2 mpa_id: 68816353 wdpa_id: 555571171
21371 2020-12-22 16:54:25.078446 count: 2 mpa_id: 5820 wdpa_id: 555542497
21372 2020-12-22 17:18:41.137411 count: 2 mpa_id: 14936 wdpa_id: 555552445
21373 2020-12-22 13:12:44.892332 count: 3 mpa_id: 10491 wdpa_id: 156297
21374 2020-12-22 20:16:58.972112 count: 2 mpa_id: 119 wdpa_id: 793
21375 2020-12-22 14:31:22.312539 count: 2 mpa_id: 7082 wdpa_id: 313496
21376 2020-12-22 15:35:05.797758 count: 2 mpa_id: 5638 wdpa_id: 555512454
21377 2020-12-22 15:42:10.889951 count

In [7]:
from importlib import reload
from wdpa import merge
reload(merge)

<module 'wdpa.merge' from '/home/mpatlas/projects/django_mpatlas/wdpa/merge.py'>

In [9]:
tas = WdpaPoly_new.objects.filter(wdpa_pid__icontains='345888')
print(tas.count())
for t in tas:
    print(t.wdpaid, t.wdpa_pid, t.name, ',', t.desig, t.marine)

sgs = WdpaPoly_new.objects.filter(name__icontains='South Georgia')
print(sgs.count())
for s in sgs:
    print(s.wdpaid, s.wdpa_pid, s.name, ',', s.desig, s.marine)


1
345888.0 345888 Terres Australes Françaises , Réserve naturelle nationale 2
2
555547601.0 555547601 South Georgia and South Sandwich Islands Marine Protected Area , Marine Protected Area 2
555610117.0 555610117 South Georgia , Country Club 0


In [8]:
remove_log = logprefix + 'removewdpa_Global_202212_log.json'
wdpa2remove = merge.getRemoveWdpaList(logfile=remove_log)

In [10]:
len(wdpa2remove)

0

In [11]:
rm_mpas = Mpa.objects.filter(wdpa_id__in=wdpa2remove).order_by('country')
len(rm_mpas)

0

In [13]:
for m in rm_mpas:
    print(m.mpa_id, m.wdpa_id, m.wdpa_pid, m.country, m.sovereign, m.is_mpa, m.no_take, m.no_take_area, m.name, m.designation_eng)

68820630 555692282 555692282 ATF FRA True Not Reported 0.0 Périmètre De Protection De La Réserve Naturelle Nationale Des Terres Australes Françaises Protected perimeter around a national nature reserve
6395 17258 17258 BHR BHR True Not Applicable 0.0 Hawar Islands Marine Protected Area
68810702 555594048 555594048 BHR BHR True Not Reported 0.0 Tubli Bay Marine Protected Area
68810701 555594047 555594047 BHR BHR True Not Reported 0.0 Reef Bul Thamah Marine Protected Area
68816740 555629467 555629467 DOM DOM True Not Reported 0.0 Cayo Terreno Wildlife Refuge
68816737 555629464 555629464 DOM DOM True Not Reported 0.0 Cayo Monte Cristo Wildlife Refuge
68816739 555629466 555629466 DOM DOM True Not Reported 0.0 Cayo Ratas Wildlife Refuge
68816735 555629462 555629462 DOM DOM True Not Reported 0.0 Cayo Arenas Wildlife Refuge
68816741 555629468 555629468 DOM DOM True Not Reported 0.0 Cayo Tororu Wildlife Refuge
68813175 555629491 555629491 DOM DOM True Not Applicable 0.0 Playa de Cabo Rojo - Pe

In [14]:
# Don't remove until we verify that we can lose these records. Canada changed wdpa_ids and/or wdpa_pids
# for lots of sites.  And Argentina's Namuncura/Burdwood Bank I/II changed ids, which breaks things for mpatlas.
merge.removeMpasByWdpaId(wdpa2remove)

In [15]:
reload(merge)

<module 'wdpa.merge' from '/home/mpatlas/projects/django_mpatlas/wdpa/merge.py'>

In [16]:
wdpa2add = merge.getAddWdpaList()

In [17]:
len(wdpa2add)

685

In [19]:
wdpapid2add = merge.getAddWdpaPidList(verbose=True)

15 wdpa_pid's processed
555744923_A : 1 processed
555744923_B : 2 processed
555744966_F : 3 processed
555744966_C : 4 processed
555744966_J : 5 processed
555744966_E : 6 processed
555744966_D : 7 processed
555744966_G : 8 processed
555744966_I : 9 processed
555744966_B : 10 processed
555744923_C : 11 processed
555744966_L : 12 processed
555744923_D : 13 processed
555744966_A : 14 processed
555744966_K : 15 processed


In [20]:
len(wdpapid2add)

15

In [132]:
# Assign records with zones to be the first zone.  Do not rerun.
# In separate notebook

In [21]:
allpid2add = wdpapid2add + [str(int(i)) for i in wdpa2add]
len(allpid2add)
WdpaPoly_new.objects.filter(wdpa_pid__in=allpid2add).count() + \
WdpaPoint_new.objects.filter(wdpa_pid__in=allpid2add).count()

698

In [22]:
unmatched_pids_poly = WdpaPoly_new.objects.filter(
    Q(wdpa_pid__in=allpid2add) | Q(wdpaid__in=wdpa2add)
).exclude(
    wdpa_pid=Func(F('wdpaid'), function='INTEGER', template='(%(expressions)s::%(function)s)::text')
)
unmatched_pids_point = WdpaPoint_new.objects.filter(
    Q(wdpa_pid__in=allpid2add) | Q(wdpaid__in=wdpa2add)
).exclude(
    wdpa_pid=Func(F('wdpaid'), function='INTEGER', template='(%(expressions)s::%(function)s)::text')
)
unmatched_pids_poly.order_by('wdpa_pid').values_list('wdpaid', 'wdpa_pid')


<QuerySet [(555744923.0, '555744923_A'), (555744923.0, '555744923_B'), (555744923.0, '555744923_C'), (555744923.0, '555744923_D'), (555744966.0, '555744966_A'), (555744966.0, '555744966_B'), (555744966.0, '555744966_C'), (555744966.0, '555744966_D'), (555744966.0, '555744966_E'), (555744966.0, '555744966_F'), (555744966.0, '555744966_G'), (555744966.0, '555744966_H'), (555744966.0, '555744966_I'), (555744966.0, '555744966_J'), (555744966.0, '555744966_K'), (555744966.0, '555744966_L')]>

In [23]:
# Set wdpa_pid for new zones
# If existing MPAtlas sites with this wdpa_id,
# set first non-rejected site to the first PID_A.
# Clear pid for all other MPAtlas sites and flag
# as orphaned zones.

wzones = []
mpasw = [float(wi) for wi in mpaset.filter(wdpa_id__isnull=False).order_by('wdpa_id').values_list('wdpa_id', flat=True)]
polyset = WdpaPoly_new.objects.filter(wdpaid__in=mpasw).only('wdpaid', 'wdpa_pid', 'name', 'desig_eng', 'iso3', 'parent_iso3')
for w in polyset:
    if w.wdpa_pid != str(int(w.wdpaid)):
        wzones.append(w.wdpaid)
wzones = list(set(wzones))
len(wzones)

171

In [24]:
# Assign mpa records that were previously unzoned to have the pid of the first zone in the updated WDPA data set for this site.
count = 0
for wid in wzones:
    zones = WdpaPoly_new.objects.filter(wdpaid=wid).only('wdpaid', 'wdpa_pid', 'name', 'desig_eng', 'iso3', 'parent_iso3')
    firstpid = zones.order_by('wdpa_pid').first().wdpa_pid
    mpaz = mpaset.filter(wdpa_id=int(wid)).order_by('mpa_id')
    m = None
    if mpaz.filter(wdpa_pid=firstpid).count() == 0:
        # no mpas match first zone pid
        if mpaz.count() == 1:
            if mpaz[0].wdpa_pid == str(mpaz[0].wdpa_id) or mpaz[0].wdpa_pid == '' or mpaz[0].wdpa_pid is None:
                # only record without specific zone, so go ahead and set it first zone
                m = mpaz[0]
        else:
            if mpaz.count() == mpaz.filter(Q(wdpa_pid=Func(F('wdpa_id'), function='INTEGER', template='(%(expressions)s::%(function)s)::text')) | Q(wdpa_pid__isnull=True) | Q(wdpa_pid='')).count():
                # more than one mpatlas mpa record with this wdpa_id
                # but none have a proper wdpa_pid different from the wdpa_id
                # so set first one to have the first zone pid
                nonrejects = mpaz.exclude(verification_state='Rejected as MPA').order_by('mpa_id')
                if nonrejects and nonrejects.count() == 1:
                    m = nonrejects[0]
                else:
                    m = mpaz[0]
    if m:
        print(m.mpa_id, m.wdpa_id, m.wdpa_pid)
        m.wdpa_pid = firstpid
        count += 1
        print(count, m.mpa_id, m.wdpa_id, m.wdpa_pid)
        m.save()


In [12]:
reload(merge)
addpoint_geolog = logprefix + 'addpoint_Global_202212_log.json'
addpoly_log = logprefix + 'addpoly_Global_202212_log.json'
addpoly_geolog = logprefix + 'addpoly_Global_202212_geo_log.json'
# addpoint_geolog = '/Users/russmo/Code/wdpa/log/addpoint_TUV_2020_log.json'
# addpoly_log = '/Users/russmo/Code/wdpa/log/addpoly_TUV_2020_v2_zerogeofix_log.json'
# addpoly_geolog = '/Users/russmo/Code/wdpa/log/addpoly_TUV_2020_v2_zerogeofix_geo_log.json'

In [27]:
points = WdpaPoint_new.objects.filter(wdpa_pid__in=allpid2add).order_by('wdpa_pid')
merge.updateMpasFromWdpaQueryset(qs=points, poly=False, logfile=None, geologfile=addpoint_geolog, dryrun=False)

1/3 adding/updating wdpa_pid 145812 with mpa_id 6860
    PID: 145812 has 11 field diffs  and GEOM diff
    Retained old MPAtlas values for: 
2/3 adding/updating wdpa_pid 555734760 with mpa_id None
    Retained old MPAtlas values for: 
3/3 adding/updating wdpa_pid 555734763 with mpa_id None
    Retained old MPAtlas values for: 


True

In [28]:
# post_save.disconnect(mpa_post_save, sender=Mpa)
polys = WdpaPoly_new.objects.filter(wdpa_pid__in=allpid2add).order_by('wdpa_pid')
merge.updateMpasFromWdpaQueryset(qs=polys, poly=True, logfile=addpoly_log, geologfile=None, dryrun=False)
# post_save.connect(mpa_post_save, sender=Mpa)

1/695 adding/updating wdpa_pid 107697 with mpa_id None
    Retained old MPAtlas values for: 
2/695 adding/updating wdpa_pid 107837 with mpa_id None
    Retained old MPAtlas values for: 
3/695 adding/updating wdpa_pid 152079 with mpa_id 3053
    PID: 152079 has 9 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
4/695 adding/updating wdpa_pid 178800 with mpa_id 68814399
    PID: 178800 has 8 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
5/695 adding/updating wdpa_pid 20668 with mpa_id 1522
    PID: 20668 has 7 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
6/695 adding/updating wdpa_pid 2583 with mpa_id 297
    PID: 2583 has 6 field diffs  and GEOM diff
    Geom areas 0.0565890169315405% dissimilar, keeping existing MPAtlas boundaries
    Retained old MPAtlas values for: mgmt_pla

80/695 adding/updating wdpa_pid 555727447 with mpa_id None
    Retained old MPAtlas values for: 
81/695 adding/updating wdpa_pid 555727516 with mpa_id None
    Retained old MPAtlas values for: 
82/695 adding/updating wdpa_pid 555727716 with mpa_id None
    Retained old MPAtlas values for: 
83/695 adding/updating wdpa_pid 555727811 with mpa_id None
    Retained old MPAtlas values for: 
84/695 adding/updating wdpa_pid 555727830 with mpa_id None
    Retained old MPAtlas values for: 
85/695 adding/updating wdpa_pid 555727989 with mpa_id None
    Retained old MPAtlas values for: 
86/695 adding/updating wdpa_pid 555728210 with mpa_id None
    Retained old MPAtlas values for: 
87/695 adding/updating wdpa_pid 555728254 with mpa_id None
    Retained old MPAtlas values for: 
88/695 adding/updating wdpa_pid 555728305 with mpa_id None
    Retained old MPAtlas values for: 
89/695 adding/updating wdpa_pid 555728339 with mpa_id None
    Retained old MPAtlas values for: 
90/695 adding/updating wdpa_pi

165/695 adding/updating wdpa_pid 555729636 with mpa_id None
    Retained old MPAtlas values for: 
166/695 adding/updating wdpa_pid 555729657 with mpa_id None
    Retained old MPAtlas values for: 
167/695 adding/updating wdpa_pid 555729670 with mpa_id None
    Retained old MPAtlas values for: 
168/695 adding/updating wdpa_pid 555729671 with mpa_id None
    Retained old MPAtlas values for: 
169/695 adding/updating wdpa_pid 555729682 with mpa_id None
    Retained old MPAtlas values for: 
170/695 adding/updating wdpa_pid 555729711 with mpa_id None
    Retained old MPAtlas values for: 
171/695 adding/updating wdpa_pid 555729715 with mpa_id None
    Retained old MPAtlas values for: 
172/695 adding/updating wdpa_pid 555729716 with mpa_id None
    Retained old MPAtlas values for: 
173/695 adding/updating wdpa_pid 555729719 with mpa_id None
    Retained old MPAtlas values for: 
174/695 adding/updating wdpa_pid 555729723 with mpa_id None
    Retained old MPAtlas values for: 
175/695 adding/updat

251/695 adding/updating wdpa_pid 555730409 with mpa_id None
    Retained old MPAtlas values for: 
252/695 adding/updating wdpa_pid 555730415 with mpa_id None
    Retained old MPAtlas values for: 
253/695 adding/updating wdpa_pid 555730418 with mpa_id None
    Retained old MPAtlas values for: 
254/695 adding/updating wdpa_pid 555730443 with mpa_id None
    Retained old MPAtlas values for: 
255/695 adding/updating wdpa_pid 555730445 with mpa_id None
    Retained old MPAtlas values for: 
256/695 adding/updating wdpa_pid 555730451 with mpa_id None
    Retained old MPAtlas values for: 
257/695 adding/updating wdpa_pid 555730457 with mpa_id None
    Retained old MPAtlas values for: 
258/695 adding/updating wdpa_pid 555730481 with mpa_id None
    Retained old MPAtlas values for: 
259/695 adding/updating wdpa_pid 555730487 with mpa_id None
    Retained old MPAtlas values for: 
260/695 adding/updating wdpa_pid 555730499 with mpa_id None
    Retained old MPAtlas values for: 
261/695 adding/updat

335/695 adding/updating wdpa_pid 555731168 with mpa_id None
    Retained old MPAtlas values for: 
336/695 adding/updating wdpa_pid 555731179 with mpa_id None
    Retained old MPAtlas values for: 
337/695 adding/updating wdpa_pid 555731193 with mpa_id None
    Retained old MPAtlas values for: 
338/695 adding/updating wdpa_pid 555731194 with mpa_id None
    Retained old MPAtlas values for: 
339/695 adding/updating wdpa_pid 555731198 with mpa_id None
    Retained old MPAtlas values for: 
340/695 adding/updating wdpa_pid 555731216 with mpa_id None
    Retained old MPAtlas values for: 
341/695 adding/updating wdpa_pid 555731224 with mpa_id None
    Retained old MPAtlas values for: 
342/695 adding/updating wdpa_pid 555731238 with mpa_id None
    Retained old MPAtlas values for: 
343/695 adding/updating wdpa_pid 555731245 with mpa_id None
    Retained old MPAtlas values for: 
344/695 adding/updating wdpa_pid 555731258 with mpa_id None
    Retained old MPAtlas values for: 
345/695 adding/updat

420/695 adding/updating wdpa_pid 555731847 with mpa_id None
    Retained old MPAtlas values for: 
421/695 adding/updating wdpa_pid 555731862 with mpa_id None
    Retained old MPAtlas values for: 
422/695 adding/updating wdpa_pid 555731866 with mpa_id None
    Retained old MPAtlas values for: 
423/695 adding/updating wdpa_pid 555731874 with mpa_id None
    Retained old MPAtlas values for: 
424/695 adding/updating wdpa_pid 555731876 with mpa_id None
    Retained old MPAtlas values for: 
425/695 adding/updating wdpa_pid 555731877 with mpa_id None
    Retained old MPAtlas values for: 
426/695 adding/updating wdpa_pid 555731878 with mpa_id None
    Retained old MPAtlas values for: 
427/695 adding/updating wdpa_pid 555731884 with mpa_id None
    Retained old MPAtlas values for: 
428/695 adding/updating wdpa_pid 555731891 with mpa_id None
    Retained old MPAtlas values for: 
429/695 adding/updating wdpa_pid 555731919 with mpa_id None
    Retained old MPAtlas values for: 
430/695 adding/updat

506/695 adding/updating wdpa_pid 555732511 with mpa_id None
    Retained old MPAtlas values for: 
507/695 adding/updating wdpa_pid 555732520 with mpa_id None
    Retained old MPAtlas values for: 
508/695 adding/updating wdpa_pid 555732525 with mpa_id None
    Retained old MPAtlas values for: 
509/695 adding/updating wdpa_pid 555732529 with mpa_id None
    Retained old MPAtlas values for: 
510/695 adding/updating wdpa_pid 555732530 with mpa_id None
    Retained old MPAtlas values for: 
511/695 adding/updating wdpa_pid 555732535 with mpa_id None
    Retained old MPAtlas values for: 
512/695 adding/updating wdpa_pid 555732549 with mpa_id None
    Retained old MPAtlas values for: 
513/695 adding/updating wdpa_pid 555732551 with mpa_id None
    Retained old MPAtlas values for: 
514/695 adding/updating wdpa_pid 555732558 with mpa_id None
    Retained old MPAtlas values for: 
515/695 adding/updating wdpa_pid 555732560 with mpa_id None
    Retained old MPAtlas values for: 
516/695 adding/updat

590/695 adding/updating wdpa_pid 555733256 with mpa_id None
    Retained old MPAtlas values for: 
591/695 adding/updating wdpa_pid 555733260 with mpa_id None
    Retained old MPAtlas values for: 
592/695 adding/updating wdpa_pid 555733262 with mpa_id None
    Retained old MPAtlas values for: 
593/695 adding/updating wdpa_pid 555733281 with mpa_id None
    Retained old MPAtlas values for: 
594/695 adding/updating wdpa_pid 555733283 with mpa_id None
    Retained old MPAtlas values for: 
595/695 adding/updating wdpa_pid 555733306 with mpa_id None
    Retained old MPAtlas values for: 
596/695 adding/updating wdpa_pid 555733314 with mpa_id None
    Retained old MPAtlas values for: 
597/695 adding/updating wdpa_pid 555733330 with mpa_id None
    Retained old MPAtlas values for: 
598/695 adding/updating wdpa_pid 555733344 with mpa_id None
    Retained old MPAtlas values for: 
599/695 adding/updating wdpa_pid 555733358 with mpa_id None
    Retained old MPAtlas values for: 
600/695 adding/updat

675/695 adding/updating wdpa_pid 555744966_C with mpa_id None
    Retained old MPAtlas values for: 
676/695 adding/updating wdpa_pid 555744966_D with mpa_id None
    Retained old MPAtlas values for: 
677/695 adding/updating wdpa_pid 555744966_E with mpa_id None
    Retained old MPAtlas values for: 
678/695 adding/updating wdpa_pid 555744966_F with mpa_id None
    Retained old MPAtlas values for: 
679/695 adding/updating wdpa_pid 555744966_G with mpa_id None
    Retained old MPAtlas values for: 
680/695 adding/updating wdpa_pid 555744966_I with mpa_id None
    Retained old MPAtlas values for: 
681/695 adding/updating wdpa_pid 555744966_J with mpa_id None
    Retained old MPAtlas values for: 
682/695 adding/updating wdpa_pid 555744966_K with mpa_id None
    Retained old MPAtlas values for: 
683/695 adding/updating wdpa_pid 555744966_L with mpa_id None
    Retained old MPAtlas values for: 
684/695 adding/updating wdpa_pid 555745141 with mpa_id None
    Retained old MPAtlas values for: 
68

True

In [29]:
bad = WdpaPoly_new.objects.get(wdpa_pid='555643543')
bg = bad.geom
bg.num_coords

bad = WdpaPoly_new.objects.get(wdpa_pid='555643544')
bg = bad.geom
bg.num_coords

2833099

In [13]:
reload(merge)
updatepoint_geolog = logprefix + 'updatepoint_Global_202212_log.json'
updatepoly_log = logprefix + 'updatepoly_Global_202212_log.json'
updatepoly_geolog = logprefix + 'updatepoly_Global_202212_geo_log.json'
# updatepoint_geolog = '/Users/russmo/Code/wdpa/log/updatepoint_TUV_2010_v3_geo_log.json'
# updatepoly_log = '/Users/russmo/Code/wdpa/log/updatepoly_TUV_2019_v3_log.json'
# updatepoly_geolog = '/Users/russmo/Code/wdpa/log/updatepoly_TUV_2019_v3_geo_log.json'

In [31]:
# wdpa_filter = (
# #     Q(iso3__icontains='USA') | Q(parent_iso3__icontains='USA') |
# #     Q(iso3__icontains='UMI') | Q(parent_iso3__icontains='UMI') |
# #     Q(iso3__icontains='VIR') | Q(parent_iso3__icontains='VIR') |
# #     Q(iso3__icontains='PRI') | Q(parent_iso3__icontains='PRI') |
# #     Q(iso3__icontains='ASM') | Q(parent_iso3__icontains='ASM') |
# #     Q(iso3__icontains='GUM') | Q(parent_iso3__icontains='GUM') |
# #     Q(iso3__icontains='MNP') | Q(parent_iso3__icontains='MNP') |
#     Q(iso3__icontains='MEX') | Q(iso3__icontains='CHL') | Q(iso3__icontains='IDN') | 
#     Q(iso3__icontains='CHN') | Q(iso3__icontains='JPN') | 
#     Q(parent_iso3__icontains='MEX') | Q(parent_iso3__icontains='CHL') | Q(parent_iso3__icontains='IDN') |
#     Q(parent_iso3__icontains='CHN') | Q(parent_iso3__icontains='JPN') #|
# #     Q(iso3__icontains='FRA') | Q(parent_iso3__icontains='FRA') |
# #     Q(iso3__icontains='ATF') | Q(iso3__icontains='BLM') | Q(iso3__icontains='GLP') |
# #     Q(iso3__icontains='GUF') | Q(iso3__icontains='MAF') | Q(iso3__icontains='MTQ') |
# #     Q(iso3__icontains='MYT') | Q(iso3__icontains='NCL') | Q(iso3__icontains='PYF') |
# #     Q(iso3__icontains='REU') | Q(iso3__icontains='SHN') | Q(iso3__icontains='SYC') |
# #     Q(iso3__icontains='AUS') | Q(parent_iso3__icontains='AUS') |
# #     Q(iso3__icontains='ZAF') | Q(parent_iso3__icontains='ZAF') |
# #     Q(iso3__icontains='CAN') | Q(parent_iso3__icontains='CAN') |
# #     Q(iso3__icontains='GBR') | Q(parent_iso3__icontains='GBR') |
# #     Q(iso3__icontains='AIA') | Q(iso3__icontains='BMU') | Q(iso3__icontains='CYM') |
# #     Q(iso3__icontains='FLK') | Q(iso3__icontains='GIB') | Q(iso3__icontains='IMN') |
# #     Q(iso3__icontains='IOT') | Q(iso3__icontains='JEY') | Q(iso3__icontains='MSR') |
# #     Q(iso3__icontains='PCN') | Q(iso3__icontains='SGS') | Q(iso3__icontains='SHN') |
# #     Q(iso3__icontains='TCA') | Q(iso3__icontains='VGB')
# )
wdpa_filter = (
    Q()
)

wdpa_exclude = (
    Q(iso3__icontains='USA') | Q(parent_iso3__icontains='USA') |
    Q(iso3__icontains='UMI') | Q(parent_iso3__icontains='UMI') |
    Q(iso3__icontains='VIR') | Q(parent_iso3__icontains='VIR') |
    Q(iso3__icontains='PRI') | Q(parent_iso3__icontains='PRI') |
    Q(iso3__icontains='ASM') | Q(parent_iso3__icontains='ASM') |
    Q(iso3__icontains='GUM') | Q(parent_iso3__icontains='GUM') |
    Q(iso3__icontains='MNP') | Q(parent_iso3__icontains='MNP')
)
polys = WdpaPoly_new.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('1','2')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
points = WdpaPoint_new.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('1','2')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
allpid2update = list(set(list(polys) + list(points)))

polys_nonmarine = WdpaPoly_new.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('0')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
points_nonmarine = WdpaPoint_new.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('0')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
allpid2update_nonmarine = list(set(list(polys_nonmarine) + list(points_nonmarine)))

allpid2update_nonmarine_inmpatlas = mpaset.filter(wdpa_pid__in=allpid2update_nonmarine).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)

allpid2update_marine012 = allpid2update + list(allpid2update_nonmarine_inmpatlas)

In [32]:
print('marine:', len(allpid2update), 'nonmarine:', len(allpid2update_nonmarine), 'all:', len(allpid2update_marine012))
print('POINTS --', 
      'marine:', WdpaPoint_new.objects.filter(wdpa_pid__in=allpid2update).count(),
      'nonmarine:', WdpaPoint_new.objects.filter(wdpa_pid__in=allpid2update_nonmarine).count()
)
print('POLYGONS --', 
      'marine:', WdpaPoly_new.objects.filter(wdpa_pid__in=allpid2update).count(),
      'nonmarine:', WdpaPoly_new.objects.filter(wdpa_pid__in=allpid2update_nonmarine).count(),
)
print('MPATLAS Records --', 
      'marine:', mpaset.filter(wdpa_pid__in=allpid2update).count(),
      'nonmarine:', mpaset.filter(wdpa_pid__in=allpid2update_nonmarine).count(),
)

marine: 16295 nonmarine: 225463 all: 20863
POINTS -- marine: 413 nonmarine: 11790
POLYGONS -- marine: 15882 nonmarine: 213673
MPATLAS Records -- marine: 16767 nonmarine: 4568


In [33]:
len(set(allpid2update_marine012))

20715

In [34]:
# All marine=1,2 sites and only marine=0 that exist in MPAtlas
updatepoints = WdpaPoint_new.objects.filter(wdpa_pid__in=allpid2update_marine012).order_by('wdpa_pid')
merge.updateMpasFromWdpaQueryset(qs=updatepoints, poly=False, logfile=None, geologfile=updatepoint_geolog, dryrun=False)

1/1874 adding/updating wdpa_pid 101838 with mpa_id 68813475
    Retained old MPAtlas values for: 
2/1874 adding/updating wdpa_pid 10720 with mpa_id 6037
    Retained old MPAtlas values for: 
3/1874 adding/updating wdpa_pid 10724 with mpa_id 6039
    PID: 10724 has 1 field diffs 
    Retained old MPAtlas values for: 
4/1874 adding/updating wdpa_pid 107333 with mpa_id 68813477
    Retained old MPAtlas values for: 
5/1874 adding/updating wdpa_pid 10753 with mpa_id 6040
    Retained old MPAtlas values for: 
6/1874 adding/updating wdpa_pid 10753 with mpa_id 7706040
    Retained old MPAtlas values for: 
7/1874 adding/updating wdpa_pid 109013 with mpa_id 68813341
    PID: 109013 has 2 field diffs 
    Retained old MPAtlas values for: calc_area calc_m_area
8/1874 adding/updating wdpa_pid 109090 with mpa_id 68813479
    Retained old MPAtlas values for: 
9/1874 adding/updating wdpa_pid 1125 with mpa_id 5851
    Retained old MPAtlas values for: 
10/1874 adding/updating wdpa_pid 1126 with mpa_id 5

    Retained old MPAtlas values for: 
73/1874 adding/updating wdpa_pid 15661 with mpa_id 68813509
    PID: 15661 has 1 field diffs 
    Retained old MPAtlas values for: 
74/1874 adding/updating wdpa_pid 156766 with mpa_id 68813510
    PID: 156766 has 1 field diffs 
    Retained old MPAtlas values for: 
75/1874 adding/updating wdpa_pid 156767 with mpa_id 68813511
    Retained old MPAtlas values for: 
76/1874 adding/updating wdpa_pid 156768 with mpa_id 68813512
    Retained old MPAtlas values for: 
77/1874 adding/updating wdpa_pid 157236 with mpa_id 68813513
    Retained old MPAtlas values for: 
78/1874 adding/updating wdpa_pid 157280 with mpa_id 68813514
    Retained old MPAtlas values for: 
79/1874 adding/updating wdpa_pid 157282 with mpa_id 68813515
    Retained old MPAtlas values for: 
80/1874 adding/updating wdpa_pid 15754 with mpa_id 6357
    Retained old MPAtlas values for: 
81/1874 adding/updating wdpa_pid 15754 with mpa_id 7706357
    Retained old MPAtlas values for: 
82/1874 ad

    Retained old MPAtlas values for: 
150/1874 adding/updating wdpa_pid 19743 with mpa_id 6458
    Retained old MPAtlas values for: 
151/1874 adding/updating wdpa_pid 19743 with mpa_id 7706458
    Retained old MPAtlas values for: 
152/1874 adding/updating wdpa_pid 198329 with mpa_id 6894
    Retained old MPAtlas values for: 
153/1874 adding/updating wdpa_pid 198337 with mpa_id 6896
    Retained old MPAtlas values for: 
154/1874 adding/updating wdpa_pid 198346 with mpa_id 6897
    Retained old MPAtlas values for: 
155/1874 adding/updating wdpa_pid 19980 with mpa_id 6459
    PID: 19980 has 1 field diffs 
    Retained old MPAtlas values for: 
156/1874 adding/updating wdpa_pid 20017 with mpa_id 6460
    Retained old MPAtlas values for: 
157/1874 adding/updating wdpa_pid 20018 with mpa_id 6461
    Retained old MPAtlas values for: 
158/1874 adding/updating wdpa_pid 2067 with mpa_id 9462
    Retained old MPAtlas values for: 
159/1874 adding/updating wdpa_pid 2068 with mpa_id 7705858
    Retai

    Retained old MPAtlas values for: 
228/1874 adding/updating wdpa_pid 315534 with mpa_id 16075
    PID: 315534 has 1 field diffs 
    Retained old MPAtlas values for: 
229/1874 adding/updating wdpa_pid 315536 with mpa_id 7132
    PID: 315536 has 1 field diffs 
    Retained old MPAtlas values for: 
230/1874 adding/updating wdpa_pid 315542 with mpa_id 7133
    PID: 315542 has 1 field diffs 
    Retained old MPAtlas values for: 
231/1874 adding/updating wdpa_pid 315545 with mpa_id 7134
    PID: 315545 has 1 field diffs 
    Retained old MPAtlas values for: 
232/1874 adding/updating wdpa_pid 315545 with mpa_id 7707134
    PID: 315545 has 1 field diffs 
    Retained old MPAtlas values for: 
233/1874 adding/updating wdpa_pid 315558 with mpa_id 7139
    Retained old MPAtlas values for: 
234/1874 adding/updating wdpa_pid 315598 with mpa_id 7153
    Retained old MPAtlas values for: 
235/1874 adding/updating wdpa_pid 315599 with mpa_id 7154
    Retained old MPAtlas values for: 
236/1874 adding

    Retained old MPAtlas values for: no_take
297/1874 adding/updating wdpa_pid 4253 with mpa_id 5935
    Retained old MPAtlas values for: 
298/1874 adding/updating wdpa_pid 4254 with mpa_id 5936
    Retained old MPAtlas values for: 
299/1874 adding/updating wdpa_pid 4254 with mpa_id 7705936
    Retained old MPAtlas values for: 
300/1874 adding/updating wdpa_pid 4255 with mpa_id 5937
    Retained old MPAtlas values for: 
301/1874 adding/updating wdpa_pid 4255 with mpa_id 7705937
    Retained old MPAtlas values for: 
302/1874 adding/updating wdpa_pid 4257 with mpa_id 5939
    Retained old MPAtlas values for: 
303/1874 adding/updating wdpa_pid 4257 with mpa_id 7705939
    PID: 4257 has 2 field diffs 
    Retained old MPAtlas values for: no_take no_take_area
304/1874 adding/updating wdpa_pid 4258 with mpa_id 7705940
    Retained old MPAtlas values for: 
305/1874 adding/updating wdpa_pid 4258 with mpa_id 5940
    Retained old MPAtlas values for: 
306/1874 adding/updating wdpa_pid 4259 with 

...

    Retained old MPAtlas values for: 
1583/1874 adding/updating wdpa_pid 555706970 with mpa_id 68818276
    Retained old MPAtlas values for: 
1584/1874 adding/updating wdpa_pid 555706971 with mpa_id 68818277
    Retained old MPAtlas values for: 
1585/1874 adding/updating wdpa_pid 555706972 with mpa_id 68818278
    Retained old MPAtlas values for: 
1586/1874 adding/updating wdpa_pid 555706973 with mpa_id 68818279
    Retained old MPAtlas values for: 
1587/1874 adding/updating wdpa_pid 555706974 with mpa_id 68818280
    Retained old MPAtlas values for: 
1588/1874 adding/updating wdpa_pid 555706975 with mpa_id 68818281
    Retained old MPAtlas values for: 
1589/1874 adding/updating wdpa_pid 555706976 with mpa_id 68818282
    Retained old MPAtlas values for: 
1590/1874 adding/updating wdpa_pid 555706977 with mpa_id 68818283
    Retained old MPAtlas values for: 
1591/1874 adding/updating wdpa_pid 555706978 with mpa_id 68818284
    Retained old MPAtlas values for: 
1592/1874 adding/updating 

    Retained old MPAtlas values for: 
1662/1874 adding/updating wdpa_pid 555707051 with mpa_id 68818355
    Retained old MPAtlas values for: 
1663/1874 adding/updating wdpa_pid 555707052 with mpa_id 68818356
    Retained old MPAtlas values for: 
1664/1874 adding/updating wdpa_pid 555707053 with mpa_id 68818357
    Retained old MPAtlas values for: 
1665/1874 adding/updating wdpa_pid 555707054 with mpa_id 68818358
    Retained old MPAtlas values for: 
1666/1874 adding/updating wdpa_pid 555707055 with mpa_id 68818359
    Retained old MPAtlas values for: 
1667/1874 adding/updating wdpa_pid 555707056 with mpa_id 68818360
    Retained old MPAtlas values for: 
1668/1874 adding/updating wdpa_pid 555707057 with mpa_id 68818361
    Retained old MPAtlas values for: 
1669/1874 adding/updating wdpa_pid 555707058 with mpa_id 68818362
    Retained old MPAtlas values for: 
1670/1874 adding/updating wdpa_pid 555707059 with mpa_id 68818363
    Retained old MPAtlas values for: 
1671/1874 adding/updating 

    Retained old MPAtlas values for: 
1741/1874 adding/updating wdpa_pid 555707130 with mpa_id 68818434
    Retained old MPAtlas values for: 
1742/1874 adding/updating wdpa_pid 555707131 with mpa_id 68818435
    Retained old MPAtlas values for: 
1743/1874 adding/updating wdpa_pid 555707132 with mpa_id 68818436
    Retained old MPAtlas values for: 
1744/1874 adding/updating wdpa_pid 555707133 with mpa_id 68818437
    Retained old MPAtlas values for: 
1745/1874 adding/updating wdpa_pid 555707134 with mpa_id 68818438
    Retained old MPAtlas values for: 
1746/1874 adding/updating wdpa_pid 555707135 with mpa_id 68818439
    Retained old MPAtlas values for: 
1747/1874 adding/updating wdpa_pid 555707136 with mpa_id 68818440
    Retained old MPAtlas values for: 
1748/1874 adding/updating wdpa_pid 555707137 with mpa_id 68818441
    Retained old MPAtlas values for: 
1749/1874 adding/updating wdpa_pid 555707138 with mpa_id 68818442
    Retained old MPAtlas values for: 
1750/1874 adding/updating 

    Retained old MPAtlas values for: calc_area calc_m_area
1821/1874 adding/updating wdpa_pid 900706 with mpa_id 7297
    Retained old MPAtlas values for: 
1822/1874 adding/updating wdpa_pid 900707 with mpa_id 7298
    Retained old MPAtlas values for: 
1823/1874 adding/updating wdpa_pid 900715 with mpa_id 7300
    Retained old MPAtlas values for: 
1824/1874 adding/updating wdpa_pid 900756 with mpa_id 7306
    Retained old MPAtlas values for: 
1825/1874 adding/updating wdpa_pid 900758 with mpa_id 7308
    Retained old MPAtlas values for: 
1826/1874 adding/updating wdpa_pid 900768 with mpa_id 7309
    Retained old MPAtlas values for: 
1827/1874 adding/updating wdpa_pid 900769 with mpa_id 7310
    Retained old MPAtlas values for: 
1828/1874 adding/updating wdpa_pid 900774 with mpa_id 7311
    Retained old MPAtlas values for: 
1829/1874 adding/updating wdpa_pid 900785 with mpa_id 7312
    Retained old MPAtlas values for: 
1830/1874 adding/updating wdpa_pid 900787 with mpa_id 7313
    Retai

True

In [35]:
# Chilean site Kawésqar has a feature geometry with about 3936041 vertices
# It swamps the geodatabase and GeoDjango on feature save postprocessing and other tasks
# Use this previously simplified feature instead
kawesqar_wdpa_pid = 555643543
kawesqar_mpa_id = 68813461
kw = WdpaPoly_new.objects.get(wdpa_pid=kawesqar_wdpa_pid)
kw_old = WdpaPoly_prev.objects.get(wdpa_pid=kawesqar_wdpa_pid)
km = Mpa.objects.get(mpa_id=kawesqar_mpa_id)
print(kw.geom.num_coords, kw_old.geom.num_coords, km.geom.num_coords)
kw_geom = kw.geom.clone()
kw.geom = km.geom
kw_old.geom = km.geom
kw.save()
kw_old.save()
print(kw.geom.num_coords, kw_old.geom.num_coords, km.geom.num_coords)
print(km.name, km.designation)

3936042 288829 288829
288829 288829 288829
Kawésqar Parque Nacional


In [ ]:
chl2_wdpa_pid = 555643544
chl2_mpa_id = 68813462
cw = WdpaPoly_new.objects.get(wdpa_pid=chl2_wdpa_pid)
cw_old = WdpaPoly_prev.objects.get(wdpa_pid=chl2_wdpa_pid)
cm = Mpa.objects.get(mpa_id=chl2_mpa_id)
print(cw.geom.num_coords, cw_old.geom.num_coords, cm.geom.num_coords)
cm.name, cm.designation

In [ ]:
reload(merge)
# All marine=1,2 sites and only marine=0 that exist in MPAtlas
updatepolys = WdpaPoly_new.objects.filter(wdpa_pid__in=allpid2update_marine012).order_by('wdpa_pid')
#updatepolys = updatepolys.exclude(wdpa_pid__in=partialrunids)
merge.updateMpasFromWdpaQueryset(qs=updatepolys, poly=True, logfile=updatepoly_log, geologfile=None, dryrun=False)

1/19461 adding/updating wdpa_pid 1 with mpa_id 67700001
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
2/19461 adding/updating wdpa_pid 1 with mpa_id 1
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
3/19461 adding/updating wdpa_pid 100024 with mpa_id 6805
    PID: 100024 has 4 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: sovereign
4/19461 adding/updating wdpa_pid 10028 with mpa_id 787
    PID: 10028 has 1 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: no_take_area
5/19461 adding/updating wdpa_pid 10072 with mpa_id 788
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
6/19461 adding/updating wdpa_pid 100837 with mpa_id 7702609
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
7/19461 adding/updating wdpa_pid

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
52/19461 adding/updating wdpa_pid 101769 with mpa_id 6809
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
53/19461 adding/updating wdpa_pid 101774 with mpa_id 6810
    PID: 101774 has 3 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: sovereign
54/19461 adding/updating wdpa_pid 101775 with mpa_id 6811
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
55/19461 adding/updating wdpa_pid 101777 with mpa_id 6812
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
56/19461 adding/updating wdpa_pid 101778 with mpa_id 6813
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
57/19461 adding/updating wdpa_pid 101779 with mpa_id 6814
    Geom areas similar (0.0%), using WDPA boundaries
    Retai

99/19461 adding/updating wdpa_pid 102544 with mpa_id 2665
    PID: 102544 has 10 field diffs  and GEOM diff
    Geom areas 20.134527474040713% dissimilar, keeping existing MPAtlas boundaries
    Retained old MPAtlas values for: status_year rep_m_area rep_area calc_area no_take no_take_area marine own_type mgmt_auth geom
100/19461 adding/updating wdpa_pid 102547 with mpa_id 2666
    PID: 102547 has 11 field diffs  and GEOM diff
    Geom areas 0.4066910380836994% dissimilar, keeping existing MPAtlas boundaries
    Retained old MPAtlas values for: status_year rep_m_area rep_area calc_area calc_m_area no_take no_take_area marine own_type mgmt_auth geom
101/19461 adding/updating wdpa_pid 102562 with mpa_id 2667
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
102/19461 adding/updating wdpa_pid 102565 with mpa_id 9851
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
103/19461 adding/updating wdpa_pid 102598 w

    PID: 103423 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
143/19461 adding/updating wdpa_pid 103547 with mpa_id 2703
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
144/19461 adding/updating wdpa_pid 103547 with mpa_id 7702703
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
145/19461 adding/updating wdpa_pid 103548 with mpa_id 2704
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
146/19461 adding/updating wdpa_pid 103550 with mpa_id 9854
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
147/19461 adding/updating wdpa_pid 103556 with mpa_id 2705
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
148/19461 adding/updating wdpa_pid 10376 with mpa_id 798
    Geom areas similar (0.0%), using WDPA boundari

    PID: 106725 has 10 field diffs  and GEOM diff
    Geom areas 0.0006447545420218255% dissimilar, keeping existing MPAtlas boundaries
    Retained old MPAtlas values for: designation rep_m_area calc_area no_take no_take_area marine own_type geom
189/19461 adding/updating wdpa_pid 106741 with mpa_id 68813680
    PID: 106741 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
190/19461 adding/updating wdpa_pid 106767 with mpa_id 9855
    PID: 106767 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
191/19461 adding/updating wdpa_pid 106786 with mpa_id 2708
    PID: 106786 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
192/19461 adding/updating wdpa_pid 106787 with mpa_id 2709
    PID: 106787 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA b

...

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13375/19461 adding/updating wdpa_pid 555571180 with mpa_id 68816362
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13376/19461 adding/updating wdpa_pid 555571188 with mpa_id 68813365
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13377/19461 adding/updating wdpa_pid 555571189 with mpa_id 68808656
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13378/19461 adding/updating wdpa_pid 555571198 with mpa_id 68808657
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13379/19461 adding/updating wdpa_pid 555571200 with mpa_id 68808658
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13380/19461 adding/updating wdpa_pid 555571229 with mpa_id 68808659
    Geom areas similar (0.0%), using WDPA boun

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: no_take
13425/19461 adding/updating wdpa_pid 555571466 with mpa_id 15300
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13426/19461 adding/updating wdpa_pid 555571467 with mpa_id 15301
    PID: 555571467 has 1 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: no_take
13427/19461 adding/updating wdpa_pid 555571468 with mpa_id 15302
    PID: 555571468 has 1 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: no_take
13428/19461 adding/updating wdpa_pid 555571469 with mpa_id 15303
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13429/19461 adding/updating wdpa_pid 555571470 with mpa_id 15304
    PID: 555571470 has 1 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values 

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13472/19461 adding/updating wdpa_pid 555571779 with mpa_id 15344
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13473/19461 adding/updating wdpa_pid 555571784 with mpa_id 68813371
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13474/19461 adding/updating wdpa_pid 555571861 with mpa_id 15345
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13475/19461 adding/updating wdpa_pid 555571890 with mpa_id 15346
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13476/19461 adding/updating wdpa_pid 555571896 with mpa_id 15347
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13477/19461 adding/updating wdpa_pid 555571910 with mpa_id 15348
    Geom areas similar (0.0%), using WDPA boundaries
    Reta

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13525/19461 adding/updating wdpa_pid 555573639 with mpa_id 68813395
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13526/19461 adding/updating wdpa_pid 555573640 with mpa_id 15372
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
13527/19461 adding/updating wdpa_pid 555573643 with mpa_id 15373


IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [14]:
mpids = mpaset.filter(wdpa_id__isnull=False, wdpa_pid__isnull=False)
mpids_count = mpids.count()
count = 0
for m in mpids:
    count += 1
    try:
        w = WdpaPoly_new.objects.filter(wdpa_pid=m.wdpa_pid)
    except:
        try:
            w = WdpaPoint_new.objects.filter(wdpa_pid=m.wdpa_pid)
        except:
            pass
    if w.exists():
        w0 = w[0]
        mq = mpaset.filter(pk=m.pk)
        print('%s/%s mpa_id %s wdpa_pid %s updated with _wdpa values' % (count, mpids_count, m.mpa_id, w0.wdpa_pid))
        mq.update(
            no_take_wdpa=w0.no_take,
            no_take_area_wdpa=w0.no_tk_area,
        )

1/22583 mpa_id 10563 wdpa_pid 156374 updated with _wdpa values
2/22583 mpa_id 68810557 wdpa_pid 555588158 updated with _wdpa values
6/22583 mpa_id 68820636 wdpa_pid 107697 updated with _wdpa values
7/22583 mpa_id 67700001 wdpa_pid 1 updated with _wdpa values
8/22583 mpa_id 2910 wdpa_pid 145809 updated with _wdpa values
9/22583 mpa_id 68820637 wdpa_pid 107837 updated with _wdpa values
10/22583 mpa_id 1 wdpa_pid 1 updated with _wdpa values
11/22583 mpa_id 1421 wdpa_pid 18943 updated with _wdpa values
12/22583 mpa_id 11488 wdpa_pid 339935 updated with _wdpa values
13/22583 mpa_id 68811128 wdpa_pid 339952 updated with _wdpa values
14/22583 mpa_id 68810561 wdpa_pid 555588162 updated with _wdpa values
15/22583 mpa_id 6862 wdpa_pid 145815 updated with _wdpa values
16/22583 mpa_id 4032 wdpa_pid 306163 updated with _wdpa values
17/22583 mpa_id 6805 wdpa_pid 100024 updated with _wdpa values
18/22583 mpa_id 10564 wdpa_pid 156375 updated with _wdpa values
19/22583 mpa_id 7706862 wdpa_pid 145815 up

133/22583 mpa_id 68820645 wdpa_pid 555639476 updated with _wdpa values
134/22583 mpa_id 10577 wdpa_pid 156433 updated with _wdpa values
135/22583 mpa_id 10578 wdpa_pid 156436 updated with _wdpa values
136/22583 mpa_id 1431 wdpa_pid 18960 updated with _wdpa values
137/22583 mpa_id 68820646 wdpa_pid 555639562 updated with _wdpa values
138/22583 mpa_id 68811130 wdpa_pid 340019 updated with _wdpa values
139/22583 mpa_id 10580 wdpa_pid 156442 updated with _wdpa values
140/22583 mpa_id 2612 wdpa_pid 101392 updated with _wdpa values
141/22583 mpa_id 2613 wdpa_pid 101396 updated with _wdpa values
142/22583 mpa_id 68809089 wdpa_pid 555539388 updated with _wdpa values
143/22583 mpa_id 2614 wdpa_pid 101399 updated with _wdpa values
144/22583 mpa_id 68813958 wdpa_pid 146750 updated with _wdpa values
145/22583 mpa_id 68820647 wdpa_pid 555639568 updated with _wdpa values
146/22583 mpa_id 68821325 wdpa_pid 101409 updated with _wdpa values
147/22583 mpa_id 13712 wdpa_pid 555539389 updated with _wdpa v

255/22583 mpa_id 68820677 wdpa_pid 555724609 updated with _wdpa values
256/22583 mpa_id 68813965 wdpa_pid 147289 updated with _wdpa values
257/22583 mpa_id 68820678 wdpa_pid 555724876 updated with _wdpa values
258/22583 mpa_id 68809887 wdpa_pid 341128 updated with _wdpa values
259/22583 mpa_id 12081 wdpa_pid 392994 updated with _wdpa values
260/22583 mpa_id 1443 wdpa_pid 18981 updated with _wdpa values
261/22583 mpa_id 1444 wdpa_pid 18982 updated with _wdpa values
262/22583 mpa_id 6811 wdpa_pid 101775 updated with _wdpa values
263/22583 mpa_id 2920 wdpa_pid 147294 updated with _wdpa values
264/22583 mpa_id 6812 wdpa_pid 101777 updated with _wdpa values
265/22583 mpa_id 68820679 wdpa_pid 555724975 updated with _wdpa values
266/22583 mpa_id 68814446 wdpa_pid 189820 updated with _wdpa values
267/22583 mpa_id 1445 wdpa_pid 18983 updated with _wdpa values
268/22583 mpa_id 12082 wdpa_pid 392995 updated with _wdpa values
269/22583 mpa_id 12083 wdpa_pid 392996 updated with _wdpa values
270/225

378/22583 mpa_id 13725 wdpa_pid 555539429 updated with _wdpa values
379/22583 mpa_id 2934 wdpa_pid 147321 updated with _wdpa values
380/22583 mpa_id 4076 wdpa_pid 306307 updated with _wdpa values
381/22583 mpa_id 68820703 wdpa_pid 555727096 updated with _wdpa values
382/22583 mpa_id 68812572 wdpa_pid 555588202 updated with _wdpa values
383/22583 mpa_id 68811430 wdpa_pid 555524343 updated with _wdpa values
385/22583 mpa_id 68813969 wdpa_pid 147322 updated with _wdpa values
386/22583 mpa_id 68815073 wdpa_pid 341443 updated with _wdpa values
387/22583 mpa_id 68820704 wdpa_pid 555727097 updated with _wdpa values
388/22583 mpa_id 68820705 wdpa_pid 555727143 updated with _wdpa values
389/22583 mpa_id 10587 wdpa_pid 156462 updated with _wdpa values
390/22583 mpa_id 4077 wdpa_pid 306308 updated with _wdpa values
391/22583 mpa_id 12096 wdpa_pid 393010 updated with _wdpa values
392/22583 mpa_id 68820706 wdpa_pid 555727277 updated with _wdpa values
393/22583 mpa_id 2935 wdpa_pid 147323 updated wi

501/22583 mpa_id 68820736 wdpa_pid 555729019 updated with _wdpa values
502/22583 mpa_id 68815076 wdpa_pid 341574 updated with _wdpa values
503/22583 mpa_id 13249 wdpa_pid 555531129 updated with _wdpa values
504/22583 mpa_id 3269 wdpa_pid 156516 updated with _wdpa values
505/22583 mpa_id 10603 wdpa_pid 156521 updated with _wdpa values
506/22583 mpa_id 12111 wdpa_pid 393025 updated with _wdpa values
507/22583 mpa_id 13732 wdpa_pid 555539551 updated with _wdpa values
508/22583 mpa_id 68811434 wdpa_pid 555524367 updated with _wdpa values
509/22583 mpa_id 11823 wdpa_pid 388434 updated with _wdpa values
510/22583 mpa_id 13733 wdpa_pid 555539552 updated with _wdpa values
511/22583 mpa_id 68817090 wdpa_pid 555646024 updated with _wdpa values
512/22583 mpa_id 68815077 wdpa_pid 341604 updated with _wdpa values
513/22583 mpa_id 13734 wdpa_pid 555539553 updated with _wdpa values
514/22583 mpa_id 10604 wdpa_pid 156524 updated with _wdpa values
515/22583 mpa_id 549 wdpa_pid 5809 updated with _wdpa v

...

21995/22583 mpa_id 68815787 wdpa_pid 555539518 updated with _wdpa values
21996/22583 mpa_id 15843 wdpa_pid 555578762 updated with _wdpa values
21997/22583 mpa_id 10250 wdpa_pid 155940 updated with _wdpa values
21998/22583 mpa_id 68815822 wdpa_pid 555540618 updated with _wdpa values
21999/22583 mpa_id 68811677 wdpa_pid 555533457 updated with _wdpa values
22000/22583 mpa_id 10915 wdpa_pid 182864 updated with _wdpa values
22001/22583 mpa_id 10264 wdpa_pid 155986 updated with _wdpa values
22002/22583 mpa_id 3673 wdpa_pid 302000 updated with _wdpa values
22003/22583 mpa_id 11564 wdpa_pid 346063 updated with _wdpa values
22004/22583 mpa_id 11306 wdpa_pid 326601 updated with _wdpa values
22005/22583 mpa_id 68818984 wdpa_pid 555697872 updated with _wdpa values
22006/22583 mpa_id 68813676 wdpa_pid 102192 updated with _wdpa values
22007/22583 mpa_id 11546 wdpa_pid 345590 updated with _wdpa values
22008/22583 mpa_id 15424 wdpa_pid 555574960 updated with _wdpa values
22009/22583 mpa_id 68810917 wd

22122/22583 mpa_id 68814274 wdpa_pid 170119 updated with _wdpa values
22123/22583 mpa_id 11224 wdpa_pid 308409 updated with _wdpa values
22124/22583 mpa_id 15399 wdpa_pid 555574330 updated with _wdpa values
22125/22583 mpa_id 1001 wdpa_pid 12797 updated with _wdpa values
22126/22583 mpa_id 68812381 wdpa_pid 555579622 updated with _wdpa values
22127/22583 mpa_id 15711 wdpa_pid 555578614 updated with _wdpa values
22128/22583 mpa_id 4342 wdpa_pid 309288 updated with _wdpa values
22129/22583 mpa_id 9944 wdpa_pid 149804 updated with _wdpa values
22130/22583 mpa_id 68808885 wdpa_pid 555599469 updated with _wdpa values
22131/22583 mpa_id 68812928 wdpa_pid 555622274 updated with _wdpa values
22132/22583 mpa_id 7707425 wdpa_pid 902812 updated with _wdpa values
22134/22583 mpa_id 68815310 wdpa_pid 388297 updated with _wdpa values
22135/22583 mpa_id 13173 wdpa_pid 555529887 updated with _wdpa values
22136/22583 mpa_id 68814238 wdpa_pid 169606 updated with _wdpa values
22137/22583 mpa_id 12971 wdp

22251/22583 mpa_id 68812375 wdpa_pid 555579612 updated with _wdpa values
22252/22583 mpa_id 68811646 wdpa_pid 555532824 updated with _wdpa values
22253/22583 mpa_id 15982 wdpa_pid 555579754 updated with _wdpa values
22254/22583 mpa_id 68816171 wdpa_pid 555565162 updated with _wdpa values
22255/22583 mpa_id 10956 wdpa_pid 183033 updated with _wdpa values
22256/22583 mpa_id 12994 wdpa_pid 555528002 updated with _wdpa values
22257/22583 mpa_id 1332 wdpa_pid 17747 updated with _wdpa values
22258/22583 mpa_id 68812755 wdpa_pid 555593075 updated with _wdpa values
22259/22583 mpa_id 3860 wdpa_pid 304473 updated with _wdpa values
22260/22583 mpa_id 5938 wdpa_pid 4256 updated with _wdpa values
22261/22583 mpa_id 68812227 wdpa_pid 555562151 updated with _wdpa values
22262/22583 mpa_id 5173 wdpa_pid 356912 updated with _wdpa values
22263/22583 mpa_id 68815505 wdpa_pid 396309 updated with _wdpa values
22264/22583 mpa_id 2025 wdpa_pid 63708 updated with _wdpa values
22265/22583 mpa_id 68811100 wdpa

22380/22583 mpa_id 68816220 wdpa_pid 555565890 updated with _wdpa values
22381/22583 mpa_id 68809806 wdpa_pid 139875 updated with _wdpa values
22382/22583 mpa_id 15474 wdpa_pid 555575444 updated with _wdpa values
22383/22583 mpa_id 68816066 wdpa_pid 555561972 updated with _wdpa values
22384/22583 mpa_id 68819838 wdpa_pid 555720771 updated with _wdpa values
22385/22583 mpa_id 68819839 wdpa_pid 555720773 updated with _wdpa values
22386/22583 mpa_id 2880 wdpa_pid 140589 updated with _wdpa values
22387/22583 mpa_id 11035 wdpa_pid 183280 updated with _wdpa values
22388/22583 mpa_id 68819843 wdpa_pid 555720803 updated with _wdpa values
22389/22583 mpa_id 68819844 wdpa_pid 555720804 updated with _wdpa values
22390/22583 mpa_id 10244 wdpa_pid 155809 updated with _wdpa values
22391/22583 mpa_id 68819848 wdpa_pid 555721445 updated with _wdpa values
22392/22583 mpa_id 10200 wdpa_pid 155492 updated with _wdpa values
22393/22583 mpa_id 13209 wdpa_pid 555529970 updated with _wdpa values
22394/22583 

22508/22583 mpa_id 656 wdpa_pid 8720 updated with _wdpa values
22509/22583 mpa_id 15729 wdpa_pid 555578632 updated with _wdpa values
22510/22583 mpa_id 7700909 wdpa_pid 11851 updated with _wdpa values
22511/22583 mpa_id 682 wdpa_pid 8794 updated with _wdpa values
22512/22583 mpa_id 10949 wdpa_pid 182999 updated with _wdpa values
22513/22583 mpa_id 12734 wdpa_pid 555525804 updated with _wdpa values
22514/22583 mpa_id 7330 wdpa_pid 900850 updated with _wdpa values
22515/22583 mpa_id 68811490 wdpa_pid 555526966 updated with _wdpa values
22516/22583 mpa_id 12922 wdpa_pid 555527815 updated with _wdpa values
22517/22583 mpa_id 12924 wdpa_pid 555527818 updated with _wdpa values
22518/22583 mpa_id 12968 wdpa_pid 555527938 updated with _wdpa values
22519/22583 mpa_id 7702532 wdpa_pid 95308 updated with _wdpa values
22520/22583 mpa_id 68814013 wdpa_pid 150494 updated with _wdpa values
22521/22583 mpa_id 7702546 wdpa_pid 95357 updated with _wdpa values
22522/22583 mpa_id 68811724 wdpa_pid 5555372

mpaset.filter(wdpa_pid__isnull=False).update(
    no_take_wdpa=F('no_take'), no_take_area_wdpa=F('no_take_area')
)

In [15]:
nt = ('All', 'Part', 'None')
ntupdate = mpaset.filter(wdpa_pid__isnull=False).filter(
    (~Q(no_take_wdpa__in=('All')) & Q(no_take_mpatlas__in=('All')))
    | (~Q(no_take_wdpa__in=('All', 'Part')) & Q(no_take_mpatlas__in=('All', 'Part')))
    | (Q(no_take_wdpa__in=('Not Applicable')) & Q(no_take_mpatlas__in=('All', 'Part', 'None')))
)
ntupdate.update(no_take=F('no_take_mpatlas'))

312

In [16]:
ntareaupdate = mpaset.filter(wdpa_pid__isnull=False).filter(
    Q(no_take_area_mpatlas__isnull=False) &
    (
        Q(no_take_area_wdpa__isnull=True)
        | Q(no_take_area_mpatlas__gt=F('no_take_area_wdpa'))
    )
)
ntareaupdate.update(no_take_area=F('no_take_area_mpatlas'))

1591

In [17]:
ntchanges = ntupdate | ntareaupdate
for n in ntchanges:
    print(n.mpa_id, n.wdpa_id, n.wdpa_pid, n.name, n.designation, n.designation_eng, n.no_take_wdpa, n.no_take_mpatlas, n.no_take_area_wdpa, n.no_take_area_mpatlas)

67704045 306179 306179 Aliwal Shoal Marine Protected Area Marine Protected Area Marine Protected Area Not Reported Part 0.0 0.0
67704044 306178 306178 Table Mountain National Park Marine Protected Area Marine Protected Area Marine Protected Area Not Reported Part 0.0 56.4
2615 101409 101409_A Alto Golfo de California y Delta del Río Colorado - Core Zone Reserva de la Biósfera Biosphere Reserve Not Reported All 0.0 0.0
1204 14691 14691 Riserva naturale marina di Miramare nel Golfo di Trieste Riserva Naturale Marina e Aree Naturali Marine Protette Natural Marine Reserve and Natural Protected Marine Areas Not Reported Not Reported 0.0 0.3
2728 108125 108125_A Zona marina del Archipiélago de Espíritu Santo Parque Nacional National Park Not Reported Part 0.0 0.0
68817967 555706658 555706658 Lapazhinka Lapazhin  Natural Monument Not Reported Not Applicable None 0.0
68818346 555707042 555707042 Peshhera Truba Peshhe a Tru Natural Monument Not Reported Not Applicable None 0.0
4872 342345 34234

68813548 182403 182403 Pylli i Zvernecit Monument Natyre Nature Monument (Category III IUCN) Not Reported Not Reported None 0.0
68813549 182594 182594 Shpella e Krevenicës Monument Natyre Nature Monument (Category III IUCN) Not Reported Not Applicable None 0.0
68813550 18261 18261 Michael Corbasson Territorial Park Territorial Park Not Reported Not Reported None 0.0
68813551 182664 182664 Tarraca e Greçës Monument Natyre Nature Monument (Category III IUCN) Not Reported Not Applicable None 0.0
68813552 18919 18919 Lake Letas Conservation Area Conservation Area Not Reported Not Reported None 0.0
6925 220024 220024 L'Ilot Casy (Réserve spéciale marine de la baie de Prony) Special Marine Reserve Special Marine Reserve All All 1.0 1.45
7706928 220028 220028 Bellinghausen (Motu One) Territorial Reserve Territorial Reserve All All 9.0 9.6
6928 220028 220028 Bellinghausen (Motu One) Territorial Reserve Territorial Reserve All All 9.0 9.6
68813595 302575 302575 Cedar - Fir Protected Area Protec

68817316 555705997 555705997 Usadebnyj park d. Pushkino Us debnyj par Not Defined Not Reported Not Applicable None 0.0
68817317 555705998 555705998 Gruppa velikovozrastnyh derev`ev v PKiO im. Kirova Gruppa v likovoz Natural Monument Not Reported Not Applicable None 0.0
68817318 555705999 555705999 Gruppa topolej Bolle Gruppa t polej B Natural Monument Not Reported Not Applicable None 0.0
68817319 555706000 555706000 Velikovozrastnoe derevo oreha greckogo Velikovo rastnoe Natural Monument Not Reported Not Applicable None 0.0
68817320 555706001 555706001 Ozero Mogotoevo Ozero Mogo oevo Unique Lake Not Reported Not Applicable None 0.0
68817321 555706002 555706002 Ozero Viani Ozero Vi ni Natural Monument Not Reported Not Applicable None 0.0
68817322 555706004 555706004 Dzhumalinskij teplyj klyuch Dzhumali ski  te Natural Monument Not Reported Not Applicable None 0.0
68817323 555706005 555706005 Velikovozrastnoe derevo sosny Sosnovskogo Velikovo rastnoe Natural Monument Not Reported Not App

68817458 555706143 555706143 Skaly Sem` brat`ev Skaly Se ` brat` Natural Monument Not Reported Not Applicable None 0.0
68817461 555706146 555706146 Bel`gijskaya shtol`nya Bel`gijs ay  sht Natural Monument Not Reported Not Applicable None 0.0
68817462 555706147 555706147 Rodnik u s. Goreloe Rodnik u s. Gore Natural Monument Not Reported Not Applicable None 0.0
68817463 555706148 555706148 Klyuchevye bolota Klyuchev e bolo Natural Monument Not Reported Not Applicable None 0.0
68817466 555706151 555706151 Kamennyj grib Kamennyj grib Natural Monument Not Reported Not Applicable None 0.0
68817467 555706152 555706152 Suadagskaya peshhera-istochnik Suadagsk y  pesh Natural Monument Not Reported Not Applicable None 0.0
68817468 555706153 555706153 Gora Kurkak hr. Kurkak Gora Kur ak hr.  Natural Monument Not Reported Not Applicable None 0.0
68817471 555706156 555706156 Gvardejskij park Gvardejs ij park Natural Monument Not Reported Not Applicable None 0.0
68817472 555706157 555706157 Komsomol`s

68817638 555706326 555706326 Uchastok r. Savala Uchasto  .  Sava Natural Monument Not Reported Not Applicable None 0.0
68817641 555706329 555706329 Tamiskskij kan`on Tamisksk j kan`o Natural Monument Not Reported Not Applicable None 0.0
68817645 555706333 555706333 Mineral`nyj istochnik Kliat Mineral` yj isto Natural Monument Not Reported Not Applicable None 0.0
68817646 555706334 555706334 Kurort YAmkun Kurort Y mku Natural Monument Not Reported Not Applicable None 0.0
68817647 555706335 555706335 SHilkinskaya peshhera SHilkins a a pes Natural Monument Not Reported Not Applicable None 0.0
68817648 555706336 555706336 Liman Poperechnyj Liman Po erechny Natural Monument Not Reported Not Applicable None 0.0
68817651 555706339 555706339 Otpechatki ryb v tretichnyh glinah Otpechat   ry    Natural Monument Not Reported Not Applicable None 0.0
68817649 555706337 555706337 Kabanij Kabanij State Natural Zakaznik Not Reported Not Applicable None 0.0
68817652 555706340 555706340 Ostanec podvodno

...

15340 555571506 555571506 Yamaguchi Prefectural Fisheries Coordination Regulations Article35 (iv) of the table 保護水面 Protected Water Surface Not Reported All 0.0 0.0
11171 196471 196471 Krajinski park Strunjan krajinski park Landscape Park Not Reported Part 0.0 0.0
67704213 306779 306779 Cabo Pulmo Parque Nacional National Park Not Reported All 0.0 71.0
5296 478591 478591 Parque Estadual Do Prelado Parque Park Not Applicable All 0.0 0.0
68808206 555594012 555594012 Penghu County Mao Islet 野生動物重要棲息環境 Major Wildlife Habitat Not Reported All 0.0 0.0
3117 152500 152500 2001644 Gålö Naturreservat Nature Reserve Not Reported Part 0.0 0.0
60000131 881 881 Tsitsikamma National Park National Park Not Reported Part 0.0 None
67704047 306181 306181 Pondoland Marine Protected Area Marine Protected Area Marine Protected Area Not Reported Part 0.0 0.0
9904 147297 147297 Guadeloupe Parc national, zone cœur National Park - Core Area Not Reported All 0.0 0.0
2663 102534 102534_A Pulu Keeling National Par

9659 555547753 555547753 Petu Island Marine Protected Area Marine Protected Area All All 1.0 1.2
68813630 555558400 555558400 Sistema de Humedales de la Isla de Utila Ramsar Site, Wetland of International Importance Ramsar Site, Wetland of International Importance Not Reported Not Reported None 0.0
68813631 555558412 555558412 Mastadfjellet Ramsar Site, Wetland of International Importance Ramsar Site, Wetland of International Importance Not Reported Not Reported None 0.0
68813636 555558423 555558423 Las Piñas-Parañaque Critical Habitat and Ecotourism Area Ramsar Site, Wetland of International Importance Ramsar Site, Wetland of International Importance Not Reported Not Reported None 0.0
68813638 555560021 555560021 Lipska pecina Spomenik prirode Natural Monument Not Reported Not Applicable None 0.0
68813635 555558419 555558419 Grunnfjorden Ramsar Site, Wetland of International Importance Ramsar Site, Wetland of International Importance Not Reported Not Reported None 0.0
68813639 5555600

68817777 555706466 555706466 Palanskie goryachie istochniki Palanski  goryac Natural Monument Not Reported Not Applicable None 0.0
68817778 555706467 555706467 Palanskie porogi Palanski  porogi Natural Monument Not Reported Not Applicable None 0.0
68817779 555706468 555706468 Severnyj i YUzhnyj proryvy Bol`shogo treshhinnogo Tolbachinskogo izverzheniya 1975-1976 gg. Severnyj i YUzhn Natural Monument Not Reported Not Applicable None 0.0
68817782 555706471 555706471 Holodnye mineral`nye istochniki Belye vodopady Holodnye mineral Natural Monument Not Reported Not Applicable None 0.0
68817783 555706472 555706472 YAr Generalka na reke Kamchatka YA  Gene alk  n  Natural Monument Not Reported Not Applicable None 0.0
68817788 555706477 555706477 Kedr Brednevskij Kedr Bre nevskij Natural Monument Not Reported Not Applicable None 0.0
68817789 555706478 555706478 Klyuch Ostrozhki Klyu h O troz Natural Monument Not Reported Not Applicable None 0.0
68817790 555706479 555706479 Mesto proizrastaniya 

68818368 555707064 555707064 Geologicheskij razrez proterozoya u gory Arguz (Geologicheskij razrez Satkinskoj svity verhnego proterozoya) Geologic eski  r Natural Monument Not Reported Not Applicable None 0.0
68818375 555707071 555707071 Nikelevyj profil` kory vyvetrivaniya na YUzhnom Urale (Novo-CHeremshanskij kar`er) Nikelevy  profil Natural Monument Not Reported Not Applicable None 0.0
68818374 555707070 555707070 Geologicheskoe obnazhenie gory Mayachnoj s drevnej faunoj Geologic esko  o Natural Monument Not Reported Not Applicable None 0.0
68818379 555707075 555707075 Ozero Smolino Ozero Sm lino Natural Monument Not Reported Not Applicable None 0.0
68818395 555707091 555707091 Dolina r. Beloj, obnazhenie kamennougol`nyh otlozhenij v d. SHerehovichi Dolina r  Beloj, Natural Monument Not Reported Not Applicable None 0.0
68818393 555707089 555707089 Uchastok vyvetrivaniya vulkanicheskih porfirov (u pos. Bogdanovka) Uchasto  vyvetri Natural Monument Not Reported Not Applicable None 0.0

1849 32669 32669 Schleswig-Holsteinisches Wattenmeer Nationalpark National Park Not Reported Part 0.0 125.0
3803 303552 303552 Malpelo Santuario de Fauna y Flora Fauna and Flora Sanctuary Not Reported All 0.0 9741.0
14510 555547863 555547863_A Nanumea Locally Managed Marine Area Locally Managed Marine Area Locally Managed Marine Area None All 0.0 2.0
7705388 555511959 555511959 Southeast Misool (Raja Ampat) Kawasan Konservasi Perairan Daerah Locally Managed Marine Area Not Reported Part 0.0 1212.1
67705394 555511967 555511967 KKPD KEPULAUAN DERAWAN DAN PERAIRAN SEKITARNYA Taman Pesisir dan Taman Pulau Kecil Coastal and Small Island Park Not Reported Part 0.0 990.0
4362 309479 309479_A Kent Group National Park National Park Not Reported All 0.0 22.0
7700290 2523 2523 Kornati Nacionalni park National Park Not Reported Part 0.0 11.0
68819734 32568 32568 Ilhas Selvagens Reserva Natural Natural Reserve Not Reported All 0.0 2687.0
7702154 67774 67774 Corner Inlet Ramsar Site, Wetland of Inte

In [18]:
ntchanges = ntupdate | ntareaupdate

import csv

nt_log = logprefix + 'notakechange_Global_202212_log.csv'
with open(nt_log, 'w', newline='') as csvfile:
    fieldnames = ['mpa_id', 'wdpa_id', 'wdpa_pid', 'name', 'designation', 'designation_eng', 'no_take_wdpa', 'no_take_mpatlas', 'no_take_area_wdpa', 'no_take_area_mpatlas']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for row in ntchanges.values(*fieldnames):
        writer.writerow(row)

In [19]:
for n in ntchanges:
    try:
        w_new = WdpaPoly_new.objects.get(wdpa_pid=n.wdpa_pid)
    except:
        w_new = WdpaPoint_new.objects.get(wdpa_pid=n.wdpa_pid)
    try:
        w_prev = WdpaPoly_prev.objects.filter(wdpa_pid=n.wdpa_pid)[0]
    except:
        try:
            w_prev = WdpaPoint_prev.objects.filter(wdpa_pid=n.wdpa_pid)[0]
        except:
            try:
                w_prev = WdpaPoly_prev.objects.filter(wdpaid=n.wdpa_id)[0]
            except:
                w_prev = WdpaPoint_prev.objects.filter(wdpaid=n.wdpa_id)[0]
    if (n.no_take == w_prev.no_take) or (n.no_take_area == w_prev.no_tk_area):
        print(w_new.name, w_new.desig, n.no_take_mpatlas, w_new.no_take, w_prev.no_take, n.no_take_area_mpatlas, w_new.no_tk_area, w_prev.no_tk_area)

Aliwal Shoal Marine Protected Area Marine Protected Area Part Not Reported Not Reported 0.0 0.0 0.0


DoesNotExist: WdpaPoint_new matching query does not exist.

In [20]:
ntchanges2 = ntupdate | ntareaupdate
ntchanges.count()

1807

In [21]:
"done"

'done'

In [53]:
merge.updateMpasFromWdpaQueryset(qs=WdpaPoly_new.objects.filter(wdpaid__in=[341532]).defer(*WdpaPoly_new.get_geom_fields()).order_by('wdpaid'), poly=True)

1/1 adding/updating wdpa_pid 341532 with mpa_id 68819799
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: mgmt_auth


True

In [95]:
mpaset = mpas_all_nogeom.exclude(
        Q(country__icontains='USA') | Q(sovereign__icontains='USA') |
        Q(country__icontains='UMI') | Q(sovereign__icontains='UMI') |
        Q(country__icontains='VIR') | Q(sovereign__icontains='VIR') |
        Q(country__icontains='PRI') | Q(sovereign__icontains='PRI') |
        Q(country__icontains='ASM') | Q(sovereign__icontains='ASM') |
        Q(country__icontains='GUM') | Q(sovereign__icontains='GUM') |
        Q(country__icontains='MNP') | Q(sovereign__icontains='MNP')
#     ).exclude(
#         Q(country__icontains='MEX') | Q(country__icontains='CHL') | Q(country__icontains='IDN') | 
#         Q(country__icontains='CHN') | Q(country__icontains='JPN') | 
#         Q(sovereign__icontains='MEX') | Q(sovereign__icontains='CHL') | Q(sovereign__icontains='IDN') |
#         Q(sovereign__icontains='CHN') | Q(sovereign__icontains='JPN')
#     ).exclude(
#         Q(country__icontains='FRA') | Q(sovereign__icontains='FRA') |
#         Q(country__icontains='ATF') | Q(country__icontains='BLM') | Q(country__icontains='GLP') |
#         Q(country__icontains='GUF') | Q(country__icontains='MAF') | Q(country__icontains='MTQ') |
#         Q(country__icontains='MYT') | Q(country__icontains='NCL') | Q(country__icontains='PYF') |
#         Q(country__icontains='REU') | Q(country__icontains='SHN') | Q(country__icontains='SYC')
#     ).exclude(
#         Q(country__icontains='AUS') | Q(sovereign__icontains='AUS') |
#         Q(country__icontains='ZAF') | Q(sovereign__icontains='ZAF') |
#         Q(country__icontains='CAN') | Q(sovereign__icontains='CAN')
#     ).exclude(
#         Q(country__icontains='GBR') | Q(sovereign__icontains='GBR') |
#         Q(country__icontains='AIA') | Q(country__icontains='BMU') | Q(country__icontains='CYM') |
#         Q(country__icontains='FLK') | Q(country__icontains='GIB') | Q(country__icontains='IMN') |
#         Q(country__icontains='IOT') | Q(country__icontains='JEY') | Q(country__icontains='MSR') |
#         Q(country__icontains='PCN') | Q(country__icontains='SGS') | Q(country__icontains='SHN') |
#         Q(country__icontains='TCA') | Q(country__icontains='VGB')
    ).filter(Q())

from mpatlas.utils import cartompa
cartompa.purgeCartoMpas()

[188,
 195,
 498,
 500,
 504,
 512,
 513,
 514,
 515,
 995,
 1429,
 1431,
 1434,
 1435,
 1436,
 1437,
 1438,
 1440,
 1445,
 1503,
 1505,
 1508,
 1509,
 1510,
 1511,
 1513,
 1851,
 1872,
 2362,
 2363,
 2364,
 2365,
 2366,
 2367,
 2369,
 2370,
 2371,
 2375,
 2378,
 2510,
 2517,
 2518,
 2519,
 2522,
 2524,
 3582,
 3819,
 3820,
 3823,
 3824,
 6871,
 6884,
 6935,
 6936,
 6938,
 6942,
 6943,
 6945,
 6946,
 6948,
 6949,
 6952,
 6955,
 6956,
 6957,
 7270,
 7283,
 7299,
 9280,
 9397,
 9398,
 9399,
 9400,
 9401,
 9402,
 9403,
 9405,
 9406,
 9407,
 9408,
 9409,
 9410,
 9411,
 9412,
 9413,
 9414,
 9415,
 9416,
 9417,
 9418,
 9419,
 9420,
 9421,
 9422,
 15058,
 15083,
 7700994,
 7700999,
 7701851,
 7702510,
 7702516,
 7702520,
 7702521,
 7703821,
 7703822,
 7703825,
 7703826,
 7705349,
 7709259]

In [94]:
cartompa.updateAllMpas(mpas=mpaset)

Processing 10 of 1987 mpa records at a time
Records [0 - 9]
Records [10 - 19]
Records [20 - 29]
Records [30 - 39]
ERROR processing mpa 68807503:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807503
Records [40 - 49]
ERROR processing mpa 68807520:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807520
ERROR processing mpa 68807504:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807504
Records [50 - 59]
Records [60 - 69]
ERROR processing mpa 68807500:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807500
ERROR processing mpa 68807495:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807495
ERROR processing mpa 60009586:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 60009586
ERROR processing mpa 60009547:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 60009547
ERROR processing mpa 60009546:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 60009546
ERROR processing mpa 60009495:  'NoneTyp

KeyboardInterrupt: 